In [1]:
import os

from dotenv import load_dotenv
# Load environment variables from openai.env file
load_dotenv("../openai.env")

# Read the OPENAI_API_KEY from the environment
api_key = os.getenv("OPENAI_API_KEY")
serpapi_key = os.getenv("SERPAPI_API_KEY")
serper_api_key = os.getenv("SERPER_API_KEY")

os.environ["OPENAI_API_KEY"] = api_key
os.environ["SERPAPI_API_KEY"] = serpapi_key
os.environ["SERPER_API_KEY"] = serper_api_key

In [2]:
from langchain_community.chat_models import ChatOpenAI
from langchain.agents import create_openai_tools_agent, AgentExecutor, tool
from langchain_core.prompts import ChatPromptTemplate, MessagesPlaceholder
from langchain_anthropic import ChatAnthropic

In [3]:
import json
import random

#load dataset
filepath = '../data/qa_data.json'
data = []
with open(filepath, 'r', encoding='utf-8') as f:
    for line in f:
        line = line.strip()
        if not line:
            continue
        obj = json.loads(line)
        data.append(obj)


In [4]:
random.seed(12)
sampled_data = random.sample(data, k=200)

In [5]:
sampled_data

[{'knowledge': 'Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).',
  'question': 'What is the birthdate of this former American football quarterback who played for the Dallas Cowboys and who was protected by his offensive tackle Mark Tuinei?',
  'right_answer': 'November 21, 1966',
  'hallucinated_answer': 'Tuinei and Aikman were teammates.'},
 {'knowledge': ' He attended Merrimack High School in Merrimack, New Hampshire.Merrimack High School (MHS) is the public seconda

In [6]:
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_openai import OpenAIEmbeddings
from langchain_chroma import Chroma

from langchain.schema import Document

def create_rag_vector_store():
    """
     Load the sampled_data entries from the preloaded SQuAD v2-style dataset,
    split them into chunks, and store them into a Chroma vector database.
    """
    # load data
    contexts = [item['knowledge'] for item in sampled_data]

    # Construct a list of Document objects
    docs = [Document(page_content=ctx, metadata={"source": "HaluEval", "index": i})
            for i, ctx in enumerate(contexts)]

    # Split the documents into chunks
    splitter = RecursiveCharacterTextSplitter(chunk_size=800, chunk_overlap=50)
    chunks = splitter.split_documents(docs)

    # Embed and store into Chroma
    vectordb = Chroma.from_documents(
        documents=chunks,
        embedding=OpenAIEmbeddings(model="text-embedding-3-small"),
        persist_directory="D:/Bristol_Study/FP/database",
        collection_name="rag_contexts"
    )

    print("HaluEval vector database created successfully (Chroma)")
    return vectordb

D:\Anaconda\envs\LongChain\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [7]:
vectordb = create_rag_vector_store()

HaluEval vector database created successfully (Chroma)


In [9]:
# create search tool use GoogleSerper
from langchain_community.utilities import GoogleSerperAPIWrapper


@tool
def search(query: str) -> str:
    """
    Use this funciton when no useful evidence is found from "get_info_from_local_db" or when the question involves real-time information.
    """
    search = GoogleSerperAPIWrapper()
    result = search.run(query)
    return result

In [10]:
# create tool get info from local database
@tool
def get_info_from_local_db(query: str):
    """
    This function must be called.
    """
    # load Chroma database
    vectordb = Chroma(
        persist_directory="D:/Bristol_Study/FP/database",
        embedding_function=OpenAIEmbeddings(model="text-embedding-3-small"),
        collection_name="rag_contexts",
    )

    retriever = vectordb.as_retriever(search_type="mmr")

    result = retriever.get_relevant_documents(query)

    return result

In [11]:
@tool
def multi_model_verify(query: str) -> str:
    """
    If use "search" fuction, must use this function.
    Use this funciton when no useful evidence is found from "get_info_from_local_db".
    """

    # get evidence by get_info_from_local_db
    try:
        docs = get_info_from_local_db.run(query)
        evidence = "\n\n".join([doc.page_content for doc in docs]) if docs else "No evidence found."
    except Exception as e:
        evidence = f"[ERROR retrieving evidence]: {str(e)}"

    # define models
    models = [
        ChatOpenAI(model="gpt-3.5-turbo", temperature=0),
        ChatOpenAI(model="gpt-4.1-nano-2025-04-14", temperature=0),
        ChatAnthropic(model="claude-3-haiku-20240307", temperature=0),
    ]

    verify_prompt = ChatPromptTemplate.from_messages([
        ("system",
         "You are a hallucination detection assistant. You are given a question, an answer, and supporting evidence.\n"
         "Your job is to determine whether the answer contains hallucinated or non-factual information, based solely on the evidence.\n\n"
         "Respond in this format:\n"
         "Judgement: Yes or No\n"
         "Reason: <your explanation>"),
        ("human",
         "Question and Answer:\n{query}\n\nEvidence:\n{evidence}")
    ])

    def extract_judgement(text: str) -> str:
        import re
        match = re.search(r"Judgement:\s*(Yes|No)", text, re.IGNORECASE)
        if match:
            return match.group(1).capitalize()
        return "Unclear"

    responses = []
    votes = []

    # judgement
    for i, model in enumerate(models):
        try:
            chain = verify_prompt | model
            response = chain.invoke({
                "query": query,
                "evidence": evidence
            })
            content = response.content.strip()
            judgement = extract_judgement(content)
            responses.append({
                "model": f"model_{i+1}",
                "judgement": judgement,
                "content": content
            })
            votes.append(judgement)
        except Exception as e:
            responses.append({
                "model": f"model_{i+1}",
                "judgement": "Unclear",
                "content": f"[ERROR] {str(e)}"
            })
            votes.append("Unclear")

    # vote
    yes_votes = votes.count("Yes")
    no_votes = votes.count("No")
    unclear_votes = votes.count("Unclear")

    if yes_votes >= 2:
        final_judgement = "Yes"
    elif no_votes >= 2:
        final_judgement = "No"
    else:
        final_judgement = "Unclear"

    # output
    model_outputs = "\n\n".join([
        f"{r['model']} - Judgement: {r['judgement']}\n{r['content']}" for r in responses
    ])

    result = (
        f"Final Judgement (by majority vote): **{final_judgement}**\n\n"
        f"Votes → Yes: {yes_votes}, No: {no_votes}, Unclear: {unclear_votes}\n\n"
        f"=== Individual Model Outputs ===\n\n{model_outputs}"
    )

    return result


In [12]:
class HalReduce:
    def __init__(self):
        # Initialize the LLM model
        self.chatmodel = ChatOpenAI(
            model="gpt-3.5-turbo",
            temperature=0,
            streaming=True,
        )

        # prompt
        self.SYSTEMPL = """
        You are a hallucination detector.Given a question and an answer, your objective is to determine if the provided answer contains non-factual or hallucinated information. You SHOULD give your judgement based on the following hallucination types and the world knowledge.

        Based on the provided knowledge, question, and answer, determine whether the answer contains any non-factual or hallucinated information.

        You must use the following tools in order:

        1. First, always call "get_info_from_local_db" to retrieve relevant evidence.
        2. If and only if no relevant information is found in the local database, then:
           - Call "search" to retrieve real-time information.
           - Also call "multi_model_verify" to perform multi-model verification.

        If use "search" fuction, must use "multi_model_verify" function.
        Always base your judgement on retrieved evidence.
        """

        self.prompt = ChatPromptTemplate.from_messages([
            ("system", self.SYSTEMPL),  # 系统消息
            ("human", "{input}"),     # 用户输入
            ("human", """
            1.Summarize the answer. If it contains non-factual information, return **No**
            2.Summarize the answer. If it is factual information, return **Yes**
            3.You must return your final judgement in the format of "**Yes**" or "**No**"."""),
            MessagesPlaceholder(variable_name='agent_scratchpad'),  # 代理的思考痕迹
        ])

        # define tools
        tools = [get_info_from_local_db, search, multi_model_verify]

        # Initialize agent
        self.agent = create_openai_tools_agent(
            self.chatmodel,
            tools=tools,
            prompt=self.prompt,
        )

        self.agent_executor = AgentExecutor(
            agent=self.agent,
            tools=tools,
            # memory=memory,
            verbose=True,
        )


    def run(self, question: str, answer: str) -> str:
        """
        Receive the three parts: knowledge, question, and answer, construct the prompt and invoke the agent.
        Ultimately, only return 'Yes' or 'No'.

        First, always call "get_info_from_local_db" to retrieve relevant evidence.
        If and only if no relevant information is found in the local database, then:
           - Call "search" to retrieve real-time information.
           - Also call "multi_model_verify" to perform multi-model verification.
        If use "search" fuction, must use "multi_model_verify" function.
        """
        prompt = (
            f"#Question#: {question}\n"
            f"#Answer#: {answer}\n"
            f"#Your Judgement#:"
        )

        result = self.agent_executor.invoke({"input": prompt})
        text = result['output'] if isinstance(result, dict) and 'output' in result else str(result)
        print(text)

        if "Yes" in text and "No" not in text:
            pred = "Yes"
        else:
            pred = "No"

        return pred



In [13]:
halReduce = HalReduce()

C:\Users\Dave\AppData\Local\Temp\ipykernel_27948\2062854714.py:4: LangChainDeprecationWarning: The class `ChatOpenAI` was deprecated in LangChain 0.0.10 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-openai package and should be used instead. To use it run `pip install -U :class:`~langchain-openai` and import as `from :class:`~langchain_openai import ChatOpenAI``.
  self.chatmodel = ChatOpenAI(


In [14]:
# evaluation
def evaluate_sample(test_data, output_path):
        """
        Perform hallucination detection on a single sample and return the result dictionary.
        """
        # write jsonl
        def dump_jsonl(obj, path, append=True):
            mode = "a" if append else "w"
            with open(path, mode, encoding="utf-8") as fw:
                fw.write(json.dumps(obj, ensure_ascii=False) + "\n")

        data = test_data

        correct = 0
        incorrect = 0
        for i in range(len(data)):
            knowledge = data[i]["knowledge"]
            question = data[i]["question"]
            hallucinated_answer = data[i]["hallucinated_answer"]
            right_answer = data[i]["right_answer"]

            if random.random() > 0.5:
                answer = hallucinated_answer
                ground_truth = "No"
            else:
                answer = right_answer
                ground_truth = "Yes"

            pred = halReduce.run(question, answer)
            if pred == ground_truth:
                correct += 1
            else:
                incorrect += 1

            result = {
                "knowledge": knowledge,
                "question": question,
                "answer": answer,
                "ground_truth": ground_truth,
                "judgement": pred
            }

            print(result)

            dump_jsonl(result, output_path, append=True)
            print(f"[{i+1}/{len(test_data)}], {knowledge}, {question}, {answer} gt={ground_truth} pred={pred}")

        total = len(data)
        print(total)
        accuracy = correct / total if total > 0 else 0.0
        print(f"{correct} correct, {incorrect} incorrect, Accuracy: {accuracy:.4f}")


In [15]:
random.seed(12)
sampled_data  = random.sample(data, k=200)
sampled_data

[{'knowledge': 'Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).',
  'question': 'What is the birthdate of this former American football quarterback who played for the Dallas Cowboys and who was protected by his offensive tackle Mark Tuinei?',
  'right_answer': 'November 21, 1966',
  'hallucinated_answer': 'Tuinei and Aikman were teammates.'},
 {'knowledge': ' He attended Merrimack High School in Merrimack, New Hampshire.Merrimack High School (MHS) is the public seconda

In [18]:
evaluate_sample(sampled_data, "../outputs/agent_results_200_1.jsonl")



> Entering new AgentExecutor chain...
1. The answer does not provide the birthdate of the former American football quarterback who played for the Dallas Cowboys and was protected by his offensive tackle Mark Tuinei.
2. The answer simply states that Tuinei and Aikman were teammates.
3. **No**

> Finished chain.
1. The answer does not provide the birthdate of the former American football quarterback who played for the Dallas Cowboys and was protected by his offensive tackle Mark Tuinei.
2. The answer simply states that Tuinei and Aikman were teammates.
3. **No**
{'knowledge': 'Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.T

In [21]:
evaluate_sample(sampled_data, "../outputs/agent_results_200_2.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'former American football quarterback who played for the Dallas Cowboys and who was protected by his offensive tackle Mark Tuinei'}`


[Document(id='21aa7ff6-e0b7-41dd-8476-5a689e3751cf', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='85b90034-bd14-451e-8948-3a5dccccc0b5', metadata={'source': 'HaluEval',

In [22]:
evaluate_sample(sampled_data, "../outputs/agent_results_200_3.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'Mark Tuinei'}`


[Document(id='9865b29c-0fed-445e-af86-1c296ab20652', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='c8909e58-3e73-4b45-abdc-c5bf6314afa2', metadata={'index': 193, 'source': 'HaluEval'}, page_content='Mark Rankin was lead vocalist with Scottish rock band Gun, who were best known for thei

In [16]:
evaluate_sample(sampled_data, "../outputs/agent_results_200_4.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'former American football quarterback who played for the Dallas Cowboys and who was protected by his offensive tackle Mark Tuinei'}`




C:\Users\Dave\AppData\Local\Temp\ipykernel_11520\2831246711.py:15: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use :meth:`~invoke` instead.
  result = retriever.get_relevant_documents(query)


[Document(id='21aa7ff6-e0b7-41dd-8476-5a689e3751cf', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='85b90034-bd14-451e-8948-3a5dccccc0b5', metadata={'index': 190, 'source': 'HaluEval'}, page_content='They were coached by head coach Mark Mangino and played their home games at Memorial Stadium in Lawrence, Kansas.Mark Thomas Mangino (born August 26, 1956) is an American football coach, who until 

In [17]:
evaluate_sample(sampled_data, "../outputs/agent_results_200_5.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'former American football quarterback birthdate Dallas Cowboys Mark Tuinei'}`


[Document(id='21aa7ff6-e0b7-41dd-8476-5a689e3751cf', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='85b90034-bd14-451e-8948-3a5dccccc0b5', metadata={'index': 190, 'source': 'HaluEval'}, page_content='They were coached by head

In [19]:
agent_acc = (0.69 + 0.655 +0.66 + 0.69 + 0.64) / 5
print(agent_acc)

0.667


In [16]:
evaluate_sample(sampled_data, "../outputs/agent_multi_results_1.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'birthdate of former American football quarterback who played for the Dallas Cowboys and was protected by Mark Tuinei'}`




C:\Users\Dave\AppData\Local\Temp\ipykernel_27948\2831246711.py:15: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use :meth:`~invoke` instead.
  result = retriever.get_relevant_documents(query)


[Document(id='21aa7ff6-e0b7-41dd-8476-5a689e3751cf', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='b73e77ff-0ba2-4a2c-8e30-1b8cc4e29c57', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 1

In [19]:
evaluate_sample(sampled_data, "../outputs/agent_multi_results_2.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'Mark Tuinei'}`


[Document(id='9865b29c-0fed-445e-af86-1c296ab20652', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='851dd734-f172-484a-8f8e-2a6a8c266beb', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tac

In [18]:
evaluate_sample(sampled_data, "../outputs/agent_multi_results_3.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'Mark Tuinei'}`


[Document(id='9865b29c-0fed-445e-af86-1c296ab20652', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='851dd734-f172-484a-8f8e-2a6a8c266beb', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tac

In [16]:
evaluate_sample(sampled_data, "../outputs/agent_multi_results_4.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'birthdate of former American football quarterback who played for the Dallas Cowboys and was protected by Mark Tuinei'}`




C:\Users\Dave\AppData\Local\Temp\ipykernel_16016\2831246711.py:15: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use :meth:`~invoke` instead.
  result = retriever.get_relevant_documents(query)


[Document(id='21aa7ff6-e0b7-41dd-8476-5a689e3751cf', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='b73e77ff-0ba2-4a2c-8e30-1b8cc4e29c57', metadata={'source': 'HaluEval', 'index': 0}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 1

In [17]:
evaluate_sample(sampled_data, "../outputs/agent_multi_results_5.jsonl")



> Entering new AgentExecutor chain...

Invoking: `get_info_from_local_db` with `{'query': 'Mark Tuinei'}`


[Document(id='9865b29c-0fed-445e-af86-1c296ab20652', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tackle in the National Football League for the Dallas Cowboys. Known as a "gentle giant", his career lasted for 15 years (1983–1997) and his ability to protect quarterback Troy Aikman and to run-block for running back Emmitt Smith helped them win Super Bowls in 1992, 1993, and 1995 and the NFC East Division in 1985 and 1992-96.Troy Kenneth Aikman (born November 21, 1966) is a former American football quarterback who played for the Dallas Cowboys in the National Football League (NFL).'), Document(id='851dd734-f172-484a-8f8e-2a6a8c266beb', metadata={'index': 0, 'source': 'HaluEval'}, page_content='Mark Pulemau Tuinei (March 31, 1960 – May 6, 1999) was an American football offensive tac

In [17]:
multi_model_acc = (0.71 + 0.705 + 0.705 + 0.71 + 0.68) / 5
print(multi_model_acc)

0.7020000000000001
